<a href="https://colab.research.google.com/github/8sheeta8/Attack_Network_AI/blob/main/XSS(8sheeta8)/XSS.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Part 0. 런타임/패키지 준비 (GPU 확인 + 설치)

In [5]:
# GPU 확인 (런타임 > 변경 > 하드웨어 가속기: GPU)
!nvidia-smi -L || echo "No GPU detected (GPU runtime 권장)"

# 필요한 패키지 설치
!pip -q install scikit-learn

GPU 0: Tesla T4 (UUID: GPU-34b5ea24-e212-667c-2f6a-4923c0ed16d0)


Part 1. (선택) 구글 드라이브 마운트 & 산출물 경로

In [6]:
USE_DRIVE = True  # False로 하면 /content에 저장
ARTIFACT_DIR = "/content/xss_gan_artifacts"

if USE_DRIVE:
    from google.colab import drive
    drive.mount('/content/drive', force_remount=True)
    ARTIFACT_DIR = "/content/drive/MyDrive/xss_gan_artifacts"

import os
os.makedirs(ARTIFACT_DIR, exist_ok=True)
print("Artifacts:", ARTIFACT_DIR)



Mounted at /content/drive
Artifacts: /content/drive/MyDrive/xss_gan_artifacts


Part 2. 데이터 업로드 (train/val/test NPY)

In [7]:
# 기대 파일명
expected = [
    "train_images.npy", "train_labels.npy",
    "val_images.npy",   "val_labels.npy",
    "test_images.npy",  "test_labels.npy"
]

import os
missing = [f for f in expected if not os.path.exists(f)]
if missing:
    from google.colab import files
    print("아래 파일 업로드:", missing)
    uploaded = files.upload()
    print("업로드 완료:", list(uploaded.keys()))

for f in expected:
    assert os.path.exists(f), f"{f} 이 필요합니다."
print("✔ NPY 확인 완료 (외부 전처리 없음)")

✔ NPY 확인 완료 (외부 전처리 없음)


Part 3. 논문-정합 구현(전체): AlexNet + MCTS-T(UCB-T) + GAN 루프

In [8]:
# -*- coding: utf-8 -*-
# 논문: "Adversarial Examples Detection for XSS Attacks based on Generative Adversarial Networks (IEEE Access, 2020)"
# - 판별기 D: AlexNet (Caffe-like: conv1/conv2 뒤 LRN 권장)
# - 생성기 G: MCTS-T (UCB-T, 위치 Dropout p=0.5, 5가지 우회 규칙)
# - GAN 루프: Pretrain D -> (G로 생성 -> D 학습) × K
# - 지표: TPR(=Recall of XSS), Precision, +F1
# - 여기서는 16×16/1ch NPY를 "그대로" 사용하고, 모델 래퍼 내부에서만 224×224/3ch로 변환합니다.

import os, math, random, urllib.parse
from typing import List, Tuple, Callable, Dict

import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader
from sklearn.metrics import confusion_matrix, precision_score, recall_score, f1_score, classification_report

# ------------------------------
# 설정 (원하면 수정 가능)
# ------------------------------
CONFIG = dict(
    SEED=42,
    BATCH_SIZE=128,
    WORKERS=2,
    PRETRAIN_EPOCHS=120,
    GAN_EPOCHS=5,
    G_STEPS=1,
    D_STEPS=1,
    MCTS_DEPTH=5,              # 논문 권장 T=5
    VARIANTS_PER_SEED=10,
    BASE_LR=0.01,              # SGD(Caffe-like)
    MOMENTUM=0.9,
    WEIGHT_DECAY=5e-4,
    STEP_LR=30,
    UCB_C1=1.0,                # ← 추가: UCB-T 탐색 상수
    UCB_C2=1.0,                # ← 추가
    USE_GROUPED_CONV=False,    # ← 선택: conv2/4/5 groups=2 사용 여부
    NULL_TOKEN="\\0",          # ← 무효 문자 기본값(가시성). 필요시 "\x00"로 바꾸세요.
)

ARTIFACT_DIR = globals().get("ARTIFACT_DIR", "/content/xss_gan_artifacts")
os.makedirs(ARTIFACT_DIR, exist_ok=True)
CHKPT_DIR = os.path.join(ARTIFACT_DIR, "checkpoints")
os.makedirs(CHKPT_DIR, exist_ok=True)

# ------------------------------
# 재현성 & 디바이스
# ------------------------------
SEED = CONFIG["SEED"]
random.seed(SEED); np.random.seed(SEED); torch.manual_seed(SEED); torch.cuda.manual_seed_all(SEED)
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
AMP = (device.type == "cuda")
if device.type == "cuda":
    torch.backends.cudnn.benchmark = True
print(f"[INFO] device={device} AMP={AMP}")

# ------------------------------
# Dataset/Loader: NPY는 그대로 (16×16/1ch). 전처리 없음.
# ------------------------------
class NpyTrafficDataset(Dataset):
    def __init__(self, images_path: str, labels_path: str):
        X = np.load(images_path)
        y = np.load(labels_path).astype(np.int64)
        assert len(X) == len(y)
        if X.ndim == 3:
            X = X[:, None, :, :]         # (N,1,H,W)
        assert X.ndim == 4
        X = X.astype(np.float32)
        if X.max() > 1.0:
            X = X / 255.0
        self.X, self.y = X, y

    def __len__(self): return len(self.y)

    def __getitem__(self, idx):
        # 전처리 없음: (1,16,16)을 그대로 반환
        x = torch.from_numpy(self.X[idx])     # (1,H,W)
        y = int(self.y[idx])
        return x, y

def make_loader(img, lbl, batch=CONFIG["BATCH_SIZE"], shuffle=False, workers=CONFIG["WORKERS"]):
    ds = NpyTrafficDataset(img, lbl)
    return DataLoader(ds, batch_size=batch, shuffle=shuffle, num_workers=workers,
                      pin_memory=(device.type=="cuda"), persistent_workers=(workers>0), drop_last=False)

# ------------------------------
# AlexNet + LRN + (옵션) Grouped Conv + Wrapper(내부 리사이즈/3ch)
# ------------------------------
class AlexNetCaffeish(nn.Module):
    def __init__(self, num_classes=2, use_grouped=False):
        super().__init__()
        g = 2 if use_grouped else 1
        self.features = nn.Sequential(
            nn.Conv2d(3, 64, kernel_size=11, stride=4, padding=2), nn.ReLU(inplace=True),
            nn.LocalResponseNorm(size=5, alpha=1e-4, beta=0.75, k=2.0),      # ← LRN 추가
            nn.MaxPool2d(kernel_size=3, stride=2),
            nn.Conv2d(64, 192, kernel_size=5, padding=2, groups=g), nn.ReLU(inplace=True),
            nn.LocalResponseNorm(size=5, alpha=1e-4, beta=0.75, k=2.0),      # ← LRN 추가
            nn.MaxPool2d(kernel_size=3, stride=2),
            nn.Conv2d(192, 384, kernel_size=3, padding=1), nn.ReLU(inplace=True),
            nn.Conv2d(384, 256, kernel_size=3, padding=1, groups=g), nn.ReLU(inplace=True),
            nn.Conv2d(256, 256, kernel_size=3, padding=1, groups=g), nn.ReLU(inplace=True),
            nn.MaxPool2d(kernel_size=3, stride=2),
        )
        self.classifier = nn.Sequential(
            nn.Dropout(0.5),
            nn.Linear(256 * 6 * 6, 4096), nn.ReLU(inplace=True),
            nn.Dropout(0.5),
            nn.Linear(4096, 4096), nn.ReLU(inplace=True),
            nn.Linear(4096, num_classes),
        )
    def forward(self, x):
        x = self.features(x)
        x = torch.flatten(x, 1)
        return self.classifier(x)

class AlexNetWrapper(nn.Module):
    """(N,1,16,16)을 받아 내부에서 (N,3,224,224)로 변환 후 AlexNet에 전달"""
    def __init__(self, use_grouped=False):
        super().__init__()
        self.backbone = AlexNetCaffeish(num_classes=2, use_grouped=use_grouped)
        self.upsample = nn.Upsample(size=(224,224), mode="bilinear", align_corners=False)
    def forward(self, x):
        # x: (N,1,16,16) 또는 (N,1,H,W)
        if x.shape[1] == 1:
            x = self.upsample(x)          # 16→224
            x = x.repeat(1,3,1,1)         # 1→3ch
        elif x.shape[2] != 224 or x.shape[3] != 224:
            x = self.upsample(x)
        return self.backbone(x)

def build_detector():
    return AlexNetWrapper(use_grouped=CONFIG["USE_GROUPED_CONV"]).to(device)

def build_opt(model):
    opt = torch.optim.SGD(model.parameters(),
                          lr=CONFIG["BASE_LR"],
                          momentum=CONFIG["MOMENTUM"],
                          weight_decay=CONFIG["WEIGHT_DECAY"])
    sched = torch.optim.lr_scheduler.StepLR(opt, step_size=CONFIG["STEP_LR"], gamma=0.1)
    return opt, sched

# ------------------------------
# 학습/평가 루틴 (TPR/Precision/F1)
# ------------------------------
def train_epoch(model, loader, opt, scaler, criterion):
    model.train()
    total=0; correct=0; loss_sum=0.0
    for xb, yb in loader:
        xb = xb.to(device, non_blocking=True); yb = yb.to(device, non_blocking=True)
        opt.zero_grad(set_to_none=True)
        with torch.cuda.amp.autocast(enabled=AMP):
            logits = model(xb)
            loss = criterion(logits, yb)
        scaler.scale(loss).backward()
        scaler.step(opt); scaler.update()
        loss_sum += loss.item()*yb.size(0)
        correct += (logits.argmax(1)==yb).sum().item()
        total += yb.size(0)
    return loss_sum/total, correct/max(1,total)

@torch.no_grad()
def eval_epoch(model, loader, print_report=False):
    model.eval()
    y_true=[]; y_pred=[]
    for xb, yb in loader:
        xb = xb.to(device, non_blocking=True)
        logits = model(xb)
        y_true.extend(yb.tolist())
        y_pred.extend(logits.argmax(1).cpu().tolist())
    tpr  = recall_score(y_true, y_pred, pos_label=1)
    prec = precision_score(y_true, y_pred, pos_label=1)
    f1   = f1_score(y_true, y_pred, pos_label=1)
    if print_report:
        print(classification_report(y_true, y_pred, target_names=["Normal(0)","XSS(1)"]))
        print("Confusion Matrix:\n", confusion_matrix(y_true, y_pred))
    return {"TPR":tpr, "Precision":prec, "F1":f1}

def pretrain_detector(model, train_loader, val_loader, epochs=CONFIG["PRETRAIN_EPOCHS"]):
    criterion = nn.CrossEntropyLoss()
    opt, sched = build_opt(model)
    scaler = torch.cuda.amp.GradScaler(enabled=AMP)
    best_tpr = -1.0
    for ep in range(1, epochs+1):
        tr_loss, tr_acc = train_epoch(model, train_loader, opt, scaler, criterion)
        m = eval_epoch(model, val_loader, print_report=False)
        sched.step()
        print(f"[PRETRAIN {ep:03d}] loss={tr_loss:.4f} acc={tr_acc:.4f} | val_TPR={m['TPR']:.4f} val_Prec={m['Precision']:.4f}")
        if m["TPR"] > best_tpr:
            best_tpr = m["TPR"]
            torch.save(model.state_dict(), os.path.join(CHKPT_DIR, "baseline_best.pt"))
    return model

# ------------------------------
# 문자열<->16x16 & 우회 규칙(5)
# ------------------------------
def string_to_image_matrix(text: str, max_len: int = 256) -> np.ndarray:
    arr = np.zeros((16,16), dtype=np.uint8)
    for i,c in enumerate(text[:max_len]):
        v = ord(c); v = v if v<=255 else 0
        arr[i//16, i%16] = v
    return arr

def hex_encode(s: str) -> str:
    out=[]
    for ch in s:
        v=ord(ch)
        if 32<=v<=126: out.append(f"&#x{v:02x}")
        else: out.append(ch)
    return "".join(out)

def dec_encode(s: str) -> str:
    out=[]
    for ch in s:
        v=ord(ch)
        if 32<=v<=126: out.append(f"&#{v}")
        else: out.append(ch)
    return "".join(out)

def url_encode(s: str) -> str:
    return urllib.parse.quote(s, safe="")

def insert_invalid_chars(s: str) -> str:
    out=[]
    for i,ch in enumerate(s):
        out.append(ch)
        if i%3==1: out.append(" ")
        elif i%5==2: out.append(CONFIG["NULL_TOKEN"])   # ← "/0" 대신 기본 "\\0"
    return "".join(out)

def case_mixture(s: str) -> str:
    return "".join(ch.upper() if random.random()<0.5 else ch.lower() for ch in s)

BYPASS_ACTIONS: List[Tuple[str, Callable[[str], str]]] = [
    ("hex", hex_encode), ("dec", dec_encode), ("url", url_encode),
    ("invalid", insert_invalid_chars), ("case", case_mixture),
]

# ------------------------------
# MCTS-T (UCB-T + position dropout)
# ------------------------------
class UCBStats:
    def __init__(self):
        self.pos_counts: Dict[int,int]     = {}
        self.pos_rewards: Dict[int,float]  = {}
        self.act_counts: Dict[str,int]     = {n:0 for n,_ in BYPASS_ACTIONS}
        self.act_rewards: Dict[str,float]  = {n:0.0 for n,_ in BYPASS_ACTIONS}

def ucb_t_value(stats: UCBStats, pos_k: int, act_j: str, C1=None, C2=None):
    if C1 is None: C1 = CONFIG["UCB_C1"]
    if C2 is None: C2 = CONFIG["UCB_C2"]
    Nk = stats.pos_counts.get(pos_k, 0); Rk = stats.pos_rewards.get(pos_k, 0.0)
    Nj = stats.act_counts.get(act_j, 0); Rj = stats.act_rewards.get(act_j, 0.0)
    Npos = sum(stats.pos_counts.values()) if sum(stats.pos_counts.values())>0 else 1
    Nact = sum(stats.act_counts.values()) if sum(stats.act_counts.values())>0 else 1
    exploit = (Rk/max(1,Nk)) * (Rj/max(1,Nj))
    explore = math.sqrt(C1*math.log(Npos)/max(1,Nk)) + math.sqrt(C2*math.log(Nact)/max(1,Nj))
    return exploit + explore

@torch.no_grad()
def detector_reward(model: nn.Module, xss_str: str) -> float:
    img = string_to_image_matrix(xss_str).astype(np.float32)
    if img.max()>1.0: img/=255.0
    ten = torch.tensor(img)[None,None,:,:].to(device)  # (1,1,16,16)
    logits = model.eval()(ten)                         # 래퍼가 내부 업샘플/3ch 처리
    prob = torch.softmax(logits, dim=1)[0,0].item()   # P(normal=0)
    return float(prob)

def mcts_t_generate(base: str, model: nn.Module, T:int=None, p_drop:float=0.5):
    if T is None: T = CONFIG["MCTS_DEPTH"]
    s = base
    stats = UCBStats()
    trace: List[Tuple[int,str]] = []
    for _ in range(T):
        cand_positions = [i for i in range(len(s)) if random.random() > p_drop] or list(range(len(s)))
        best_score=-1e9; best=None
        for pos in cand_positions:
            for name,_ in BYPASS_ACTIONS:
                val = ucb_t_value(stats, pos, name)
                if val > best_score:
                    best_score=val; best=(pos,name)
        pos,name = best
        fn = dict(BYPASS_ACTIONS)[name]
        s = s[:pos] + fn(s[pos:])   # suffix transform
        trace.append((pos,name))
    final_r = detector_reward(model, s)
    for pos,name in trace:
        stats.pos_counts[pos] = stats.pos_counts.get(pos,0)+1
        stats.act_counts[name] = stats.act_counts.get(name,0)+1
        stats.pos_rewards[pos] = stats.pos_rewards.get(pos,0.0)+final_r
        stats.act_rewards[name] = stats.act_rewards.get(name,0.0)+final_r
    return s

def generate_batch(seeds: List[str], model: nn.Module, depth:int=None, variants_per_seed:int=None) -> List[str]:
    if depth is None: depth = CONFIG["MCTS_DEPTH"]
    if variants_per_seed is None: variants_per_seed = CONFIG["VARIANTS_PER_SEED"]
    out=[]
    for s in seeds:
        for _ in range(variants_per_seed):
            out.append(mcts_t_generate(s, model, T=depth, p_drop=0.5))
    return out

def save_generated_payloads(payloads: List[str], tag="e1"):
    out_txt = os.path.join(ARTIFACT_DIR, f"paper_gen_output_{tag}.txt")
    with open(out_txt, "w", encoding="utf-8") as f:
        for p in payloads: f.write(p+"\n")
    imgs = np.stack([string_to_image_matrix(p) for p in payloads], axis=0)
    lbls = np.ones((len(payloads),), dtype=np.int64)
    gen_dir = os.path.join(ARTIFACT_DIR, f"paper_gen_npy_{tag}")
    os.makedirs(gen_dir, exist_ok=True)
    np.save(os.path.join(gen_dir, "images.npy"), imgs)
    np.save(os.path.join(gen_dir, "labels.npy"), lbls)
    print(f"[GEN] Saved {len(payloads)} payloads -> {out_txt} / {gen_dir}")
    return out_txt, os.path.join(gen_dir,"images.npy"), os.path.join(gen_dir,"labels.npy")

# ------------------------------
# GAN 루프 (Algorithm 1 유사)
# ------------------------------
def gan_train(model, train_loader, val_loader, test_loader):
    criterion = nn.CrossEntropyLoss()
    opt, sched = build_opt(model)
    scaler = torch.cuda.amp.GradScaler(enabled=AMP)

    seeds=[]
    if os.path.exists("generator_input.txt"):
        with open("generator_input.txt","r",encoding="utf-8") as f:
            seeds = [ln.strip() for ln in f if ln.strip()]
    if not seeds:
        seeds = [
            "<script>alert('XSS')</script>",
            "<img src=x onerror=alert(1)>",
            "<svg onload=alert`1`>",
            "<body onload=alert('X')>",
            "\"\\><script>alert(1)</script>",
            "<iframe src=javascript:alert(1)>",
            "<a href=javascript:alert(1)>click</a>",
            "<details open ontoggle=alert(1)>",
        ]

    best_val_tpr = -1.0
    for ge in range(1, CONFIG["GAN_EPOCHS"]+1):
        print(f"\n[GAN] ===== Epoch {ge}/{CONFIG['GAN_EPOCHS']} =====")
        # G-steps: 생성
        all_payloads=[]
        for _ in range(CONFIG["G_STEPS"]):
            adv = generate_batch(seeds, model)
            all_payloads.extend(adv)

        print("[GAN][GEN] Sample adversarial payloads (top 8):")
        for s in all_payloads[:8]: print(" -", s)
        save_generated_payloads(all_payloads, tag=f"e{ge}")

        # 생성 샘플 로더 (전처리 없음 -> 모델 래퍼가 처리)
        Xg = np.stack([string_to_image_matrix(p) for p in all_payloads], axis=0).astype(np.float32)
        if Xg.max()>1.0: Xg/=255.0
        Yg = np.ones((len(all_payloads),), dtype=np.int64)

        class GenDS(Dataset):
            def __init__(self, Xg, Yg): self.Xg=Xg; self.Yg=Yg
            def __len__(self): return len(self.Yg)
            def __getitem__(self, idx):
                x = torch.from_numpy(self.Xg[idx])[None,:,:]  # (1,16,16)
                y = int(self.Yg[idx]); return x,y

        gen_loader = DataLoader(GenDS(Xg,Yg), batch_size=CONFIG["BATCH_SIZE"], shuffle=True,
                                num_workers=CONFIG["WORKERS"], pin_memory=(device.type=="cuda"),
                                persistent_workers=(CONFIG["WORKERS"]>0))

        # D-steps: 원본+생성 혼합 학습 (모델 래퍼가 동일 변환)
        model.train()
        for _ in range(CONFIG["D_STEPS"]):
            for batch_loader in (train_loader, gen_loader):
                for xb, yb in batch_loader:
                    xb = xb.to(device, non_blocking=True); yb = yb.to(device, non_blocking=True)
                    opt.zero_grad(set_to_none=True)
                    with torch.cuda.amp.autocast(enabled=AMP):
                        logits = model(xb); loss = criterion(logits, yb)
                    scaler.scale(loss).backward(); scaler.step(opt); scaler.update()
            sched.step()

        m_val = eval_epoch(model, val_loader, print_report=False)
        print(f"[GAN] After epoch {ge}: val_TPR={m_val['TPR']:.4f} val_Prec={m_val['Precision']:.4f} (F1={m_val['F1']:.4f})")

        # ← GAN 라운드에서도 최고 TPR 체크포인트 저장
        if m_val["TPR"] > best_val_tpr:
            best_val_tpr = m_val["TPR"]
            torch.save(model.state_dict(), os.path.join(CHKPT_DIR, f"gan_best_e{ge}.pt"))

    print("\n========== FINAL TEST (after GAN training) ==========")
    m_test = eval_epoch(model, test_loader, print_report=True)
    print(f"[TEST] TPR={m_test['TPR']:.4f} Precision={m_test['Precision']:.4f} (F1={m_test['F1']:.4f})")




[INFO] device=cuda AMP=True


실행

In [9]:
# ------------------------------
# 실행 (Pretrain -> Baseline Test -> GAN)
# ------------------------------
def main():
    train_loader = make_loader("train_images.npy", "train_labels.npy", shuffle=True)
    val_loader   = make_loader("val_images.npy",   "val_labels.npy")
    test_loader  = make_loader("test_images.npy",  "test_labels.npy")

    model = build_detector()
    model = pretrain_detector(model, train_loader, val_loader, epochs=CONFIG["PRETRAIN_EPOCHS"])

    print("\n========== BASELINE TEST (before GAN) ==========")
    base = eval_epoch(model, test_loader, print_report=True)
    print(f"[BASELINE] TPR={base['TPR']:.4f} Precision={base['Precision']:.4f} (F1={base['F1']:.4f})")

    gan_train(model, train_loader, val_loader, test_loader)

if __name__ == "__main__":
    main()


/tmp/ipython-input-1439733638.py:183: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  scaler = torch.cuda.amp.GradScaler(enabled=AMP)
/tmp/ipython-input-1439733638.py:153: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.amp.autocast(enabled=AMP):
/usr/local/lib/python3.12/dist-packages/sklearn/metrics/_classification.py:1565: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, f"{metric.capitalize()} is", len(result))


[PRETRAIN 001] loss=0.5912 acc=0.7234 | val_TPR=0.0000 val_Prec=0.0000


/tmp/ipython-input-1439733638.py:153: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.amp.autocast(enabled=AMP):


[PRETRAIN 002] loss=0.2844 acc=0.8483 | val_TPR=0.8477 val_Prec=0.8705


/tmp/ipython-input-1439733638.py:153: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.amp.autocast(enabled=AMP):


...

[GAN] After epoch 3: val_TPR=0.9942 val_Prec=0.9500 (F1=0.9716)

[GAN] ===== Epoch 4/5 =====
[GAN][GEN] Sample adversarial payloads (top 8):
 - &#x&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x36&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x37&#x26&#x23&#x78&#x33&#x38&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x33&#x36&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x36&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x

/tmp/ipython-input-1439733638.py:377: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.amp.autocast(enabled=AMP):


[GAN] After epoch 4: val_TPR=0.9282 val_Prec=1.0000 (F1=0.9628)

[GAN] ===== Epoch 5/5 =====
[GAN][GEN] Sample adversarial payloads (top 8):
 - &#x26&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x36&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x36&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x37&#x26&#x23&#x78&#x33&#x38&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x33&#x37&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x33&#x38&

/tmp/ipython-input-1439733638.py:377: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.cuda.amp.autocast(enabled=AMP):


[GAN] After epoch 5: val_TPR=0.9758 val_Prec=1.0000 (F1=0.9877)

========== FINAL TEST (after GAN training) ==========
              precision    recall  f1-score   support

   Normal(0)       0.99      1.00      0.99      2769
      XSS(1)       1.00      0.97      0.98       933

    accuracy                           0.99      3702
   macro avg       0.99      0.99      0.99      3702
weighted avg       0.99      0.99      0.99      3702

Confusion Matrix:
 [[2767    2]
 [  26  907]]
[TEST] TPR=0.9721 Precision=0.9978 (F1=0.9848)


Part 4. (옵션) 생성된 페이로드/산출물 확인

In [10]:
import glob, os, textwrap, itertools

print("생성된 payload 텍스트 파일들:")
for p in sorted(glob.glob(os.path.join(ARTIFACT_DIR, "paper_gen_output_*.txt"))):
    print(" -", os.path.basename(p))

# 가장 최근 파일의 상위 20개만 미리보기
latest = sorted(glob.glob(os.path.join(ARTIFACT_DIR, "paper_gen_output_*.txt")))[-1]
print("\n샘플 미리보기 (top 20):", os.path.basename(latest))
with open(latest, "r", encoding="utf-8") as f:
    for i, line in zip(range(20), f):
        print("-", line.strip())


생성된 payload 텍스트 파일들:
 - paper_gen_output_e1.txt
 - paper_gen_output_e2.txt
 - paper_gen_output_e3.txt
 - paper_gen_output_e4.txt
 - paper_gen_output_e5.txt

샘플 미리보기 (top 20): paper_gen_output_e5.txt
- &#x26&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x36&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x36&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x32&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x37&#x26&#x23&#x78&#x33&#x38&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x37&#x38&#x26&#x23&#x78&#x33&#x33&#x26&#x23&#x78&#x33&#x37&#x26&#x23&#x78&#x32&#x36&#x26&#x23&#x78&#x32&#x33&#x26&#x23&#x78&#x3